### Segmenting and Clustering Neighborhoods in Toronto
This Notebook will do:
- Scraping data from wikipedia page using BeautifulSoup package
- Processing data


In [83]:
import numpy as np
import pandas as pd
import urllib3
from bs4 import BeautifulSoup

import matplotlib.cm as cm
import matplotlib.colors as colors

In [84]:
http = urllib3.PoolManager()
r = http.request('GET', 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')
#print (r.data)

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/urllib3/connectionpool.py:858: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)


In [85]:
#soup = BeautifulSoup(r.data, 'html.parser')
#print(soup.prettify())

In [86]:
#f = open("wiki_toronto.html", "w")
#f.write(soup.prettify())
#print ("COMPLETED: Save web html with name, wiki_toronto.html")
#f.close()

In [87]:
import re

bs = BeautifulSoup(r.data, 'html.parser')
table_body=bs.find('tbody')
#print (table_body)

#declare some list as global
neighbor_list = []
columns = []
nb_data = []

tr_rows = bs.find_all('tr')
#print (tr_rows)

In [88]:
initial=True
#print (len(tr_rows))

for tr_row in tr_rows:
    #print (tr_row)
    #print ("-----------------")
    if initial==True:
        col=[]
        th=tr_row.find_all('th')
        #print (th)
        for th_row in th:
            #print (th_row.text)
            col.append(str(th_row.text).rstrip())
        
        initial=False
        
    else:
        data=[]
        td=tr_row.find_all('td')
        #print (td)
        for td_row in td:
            #print (td_row.text)
            data.append(str(td_row.text).rstrip())
            
        #append data into list
        nb_data.append(data)
    
        #print ("*************")
        #print ("col=",col)
        #print ("data=",data)
        #print ("*************")
    
columns = col.copy()

print ("###########################")
print ("columns = ",columns)
print ("nb_data = ",nb_data)
print ("###########################")
    
print ("Completed for web scraping!")

###########################
columns =  ['Postcode', 'Borough', 'Neighbourhood']
nb_data =  [['M1A', 'Not assigned', 'Not assigned'], ['M2A', 'Not assigned', 'Not assigned'], ['M3A', 'North York', 'Parkwoods'], ['M4A', 'North York', 'Victoria Village'], ['M5A', 'Downtown Toronto', 'Harbourfront'], ['M5A', 'Downtown Toronto', 'Regent Park'], ['M6A', 'North York', 'Lawrence Heights'], ['M6A', 'North York', 'Lawrence Manor'], ['M7A', "Queen's Park", 'Not assigned'], ['M8A', 'Not assigned', 'Not assigned'], ['M9A', 'Etobicoke', 'Islington Avenue'], ['M1B', 'Scarborough', 'Rouge'], ['M1B', 'Scarborough', 'Malvern'], ['M2B', 'Not assigned', 'Not assigned'], ['M3B', 'North York', 'Don Mills North'], ['M4B', 'East York', 'Woodbine Gardens'], ['M4B', 'East York', 'Parkview Hill'], ['M5B', 'Downtown Toronto', 'Ryerson'], ['M5B', 'Downtown Toronto', 'Garden District'], ['M6B', 'North York', 'Glencairn'], ['M7B', 'Not assigned', 'Not assigned'], ['M8B', 'Not assigned', 'Not assigned'], ['M9B', 'Eto

In [89]:
#columns = col.copy()
#print (columns)
df_toronto = pd.DataFrame(columns=columns)
df_toronto.head()

len_eq_3 = [(len(item) == 3) for item in nb_data]
#len_eq_3

toronto_neiborhoods_list=[]
for i, cond in zip(range(0,len(len_eq_3)),len_eq_3):
    #print (i,cond)
    if cond==True:
        toronto_neiborhoods_list.append(nb_data[i])

#print ("Processed data: toronto_neiborhoods_list = ",toronto_neiborhoods_list)

#toronto_neighborhoods = nb_data[1:-5]
#df for 
df_toronto = pd.DataFrame(data=toronto_neiborhoods_list, columns=columns)

df_toronto.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

- Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned.

In [90]:
# only get the Borough having value, ignore 'Not assigned'
df_toronto_1 = df_toronto[(df_toronto['Borough']!='Not assigned')].reset_index(drop=True)
df_toronto_1.head(10)

Postcode           Borough     Neighbourhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M5A  Downtown Toronto       Regent Park
4      M6A        North York  Lawrence Heights
5      M6A        North York    Lawrence Manor
6      M7A      Queen's Park      Not assigned
7      M9A         Etobicoke  Islington Avenue
8      M1B       Scarborough             Rouge
9      M1B       Scarborough           Malvern

- If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park.

In [91]:
#Neighbourhood have 'Not assigned' value replace the same name of Borough
for i,item in zip(range(0,len(df_toronto_1['Neighbourhood'])),df_toronto_1['Neighbourhood']):
    #print (i,item)
    if item=='Not assigned':
        df_toronto_1.loc[i,'Neighbourhood'] = df_toronto_1.loc[i,'Borough']
        
df_toronto_1.head(10)

Postcode           Borough     Neighbourhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M5A  Downtown Toronto       Regent Park
4      M6A        North York  Lawrence Heights
5      M6A        North York    Lawrence Manor
6      M7A      Queen's Park      Queen's Park
7      M9A         Etobicoke  Islington Avenue
8      M1B       Scarborough             Rouge
9      M1B       Scarborough           Malvern

- reset index

In [92]:
df_toronto_1.reset_index(drop=True, inplace=True)
df_toronto_1.head()
print (df_toronto_1.columns)

Index(['Postcode', 'Borough', 'Neighbourhood'], dtype='object')


- More than one neighborhood can exist in one postal code area. For example, in the table on the Wikipedia page, you will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods **separated with a comma as shown in row 11** in the above table.

In [93]:
#df_toronto_1['Neighbourhood'].astype(str)
#df_toronto_1.dtypes

df_toronto_2 = df_toronto_1.groupby(by=['Postcode','Borough']).agg(lambda x: ','.join(x))
df_toronto_2.reset_index(level=['Postcode','Borough'], inplace=True)

print (df_toronto_2.columns)
df_toronto_2.head(10)

Index(['Postcode', 'Borough', 'Neighbourhood'], dtype='object')


Postcode      Borough                                  Neighbourhood
0      M1B  Scarborough                                  Rouge,Malvern
1      M1C  Scarborough           Highland Creek,Rouge Hill,Port Union
2      M1E  Scarborough                Guildwood,Morningside,West Hill
3      M1G  Scarborough                                         Woburn
4      M1H  Scarborough                                      Cedarbrae
5      M1J  Scarborough                            Scarborough Village
6      M1K  Scarborough      East Birchmount Park,Ionview,Kennedy Park
7      M1L  Scarborough                  Clairlea,Golden Mile,Oakridge
8      M1M  Scarborough  Cliffcrest,Cliffside,Scarborough Village West
9      M1N  Scarborough                     Birch Cliff,Cliffside West

- use the **.shape** method to print the number of rows of your dataframe.

In [94]:
df_toronto_2.shape
#print (df_toronto_2.columns)
#print (df_toronto_2.index)

(103, 3)

**COMPLETE DATA SCRAPING AND PROCESSING!!!**

### PART2: READ GEOGRAPHYCAL COORDINATES

In [95]:
df_geo_data = pd.read_csv("http://cocl.us/Geospatial_data")
df_geo_data.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [96]:
df_toronto_geo = pd.merge(df_toronto_1, df_geo_data, how='left', left_on='Postcode', right_on='Postal Code')
df_toronto_geo.drop('Postal Code',axis=1, inplace=True)
df_toronto_geo.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636
4      M6A        North York  Lawrence Heights  43.718518 -79.464763

In [97]:
#Groupby, neighbourhood seperated by comma.
df_toronto_geo_1 = df_toronto_geo.groupby(by=['Postcode','Borough','Latitude','Longitude']).agg(lambda x: ','.join(x))
df_toronto_geo_1.reset_index(level=['Postcode','Borough','Latitude','Longitude'], inplace=True)

#check
print (df_toronto_geo_1.columns)
print (df_toronto_geo_1.index.names)

# reorder the columns 
df_toronto_geo_2 = df_toronto_geo_1[['Postcode','Borough','Neighbourhood','Latitude','Longitude']] 
df_toronto_geo_2.head()

Index(['Postcode', 'Borough', 'Latitude', 'Longitude', 'Neighbourhood'], dtype='object')
[None]


Postcode      Borough                         Neighbourhood   Latitude  \
0      M1B  Scarborough                         Rouge,Malvern  43.806686   
1      M1C  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535   
2      M1E  Scarborough       Guildwood,Morningside,West Hill  43.763573   
3      M1G  Scarborough                                Woburn  43.770992   
4      M1H  Scarborough                             Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [98]:
# list all values of 'Borough' have Toronto|toronto
print (len(df_toronto_geo_2[df_toronto_geo_2['Borough'].str.contains("Toronto|toronto")]))
df_toronto_geo_3 = df_toronto_geo_2[df_toronto_geo_2['Borough'].str.contains("Toronto|toronto")]
df_toronto_geo_3
# However, this table can not used because Neighborhood in some rows is a list of name.
# I tried again with original df_toronto_geo dataframe
df_toronto_in_name = df_toronto_geo[df_toronto_geo['Borough'].str.contains('Toronto|toronto')]
print (len(df_toronto_in_name['Neighbourhood'].unique()))
df_toronto_in_name.head()


38
73


Postcode           Borough    Neighbourhood   Latitude  Longitude
2       M5A  Downtown Toronto     Harbourfront  43.654260 -79.360636
3       M5A  Downtown Toronto      Regent Park  43.654260 -79.360636
13      M5B  Downtown Toronto          Ryerson  43.657162 -79.378937
14      M5B  Downtown Toronto  Garden District  43.657162 -79.378937
27      M5C  Downtown Toronto   St. James Town  43.651494 -79.375418

**Then we will use "df_toronto_in_name" for clustering in the next parts.**

### PART 3: Explore Neighbourhood in Toronto

In [100]:
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

In [101]:
CLIENT_ID = 'R5XDW4WA0QHRHJHUVNJ02AXAPOTW5OED5DOTINVQKXTPRJJJ' # your Foursquare ID
CLIENT_SECRET = '4RPFM2WLGNEZPTWE1ADSEYWYZXY4GR3EQSLNGVMDN1FMKIDX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100

print('My credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentails:
CLIENT_ID: R5XDW4WA0QHRHJHUVNJ02AXAPOTW5OED5DOTINVQKXTPRJJJ
CLIENT_SECRET:4RPFM2WLGNEZPTWE1ADSEYWYZXY4GR3EQSLNGVMDN1FMKIDX


In [102]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION,
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    #print (nearby_venues)
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [103]:
#df_toronto_geo_4 = df_toronto_geo_3.groupby(by=['Borough']).mean()
#df_toronto_geo_4.reset_index(level=['Borough'],inplace=True)
#print (df_toronto_geo_4.columns)
#df_toronto_geo_4

#toronto_venues = getNearbyVenues(names=df_toronto_geo_4['Borough'],
#                                 latitudes=df_toronto_geo_4['Latitude'],
#                                 longitudes=df_toronto_geo_4['Longitude'])
#toronto_venues

In [104]:
toronto_venues = getNearbyVenues(names=df_toronto_in_name['Neighbourhood'],
                                 latitudes=df_toronto_in_name['Latitude'],
                                 longitudes=df_toronto_in_name['Longitude'])
print (toronto_venues.shape)
toronto_venues.head()

Harbourfront
Regent Park
Ryerson
Garden District
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
The Danforth West
Riverdale
Design Exchange
Toronto Dominion Centre
Brockton
Exhibition Place
Parkdale Village
The Beaches West
India Bazaar
Commerce Court
Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North
Forest Hill West
High Park
The Junction South
North Toronto West
The Annex
North Midtown
Yorkville
Parkdale
Roncesvalles
Davisville
Harbord
University of Toronto
Runnymede
Swansea
Moore Park
Summerhill East
Chinatown
Grange Park
Kensington Market
Deer Park
Forest Hill SE
Rathnelly
South Hill
Summerhill West
CN Tower
Bathurst Quay
Island airport
Harbourfront West
King and Spadina
Railway Lands
South Niagara
Rosedale
Stn A PO Boxes 25 The Esplanade
Cabbagetown
St. James Town
First Canadian Place
Underground city


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Harbourfront               43.65426              -79.360636   
1  Harbourfront               43.65426              -79.360636   
2  Harbourfront               43.65426              -79.360636   
3  Harbourfront               43.65426              -79.360636   
4  Harbourfront               43.65426              -79.360636   

                                             Venue  Venue Latitude  \
0                                 Roselle Desserts       43.653447   
1                                    Tandem Coffee       43.653559   
2  Toronto Cooper Koo Family Cherry St YMCA Centre       43.653191   
3                               Morning Glory Cafe       43.653947   
4                              Body Blitz Spa East       43.654735   

   Venue Longitude        Venue Category  
0       -79.362017                Bakery  
1       -79.361809           Coffee Shop  
2       -79.357947  Gym / Fitness Center  
3       -79.361149        Breakfast Spot  
4       -79.359874                   Spa

In [105]:
!conda install -c conda-forge folium=0.5.0 --yes
!conda install -c conda-forge geopy --yes 

Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
folium                    0.5.0                      py_0    conda-forge
Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
geopy                     1.19.0                     py_0    conda-forge


In [106]:
import folium
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

#get Toronto coordinates
address = 'Toronto City'

geolocator = Nominatim(user_agent="trt_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, venue_category, neighborhood in zip(toronto_venues['Venue Latitude'], toronto_venues['Venue Longitude'], toronto_venues['Venue Category'], toronto_venues['Neighborhood']):
    #print (lat,lng,borough,neighborhood)
    label = '{}, {}'.format(neighborhood,venue_category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)
    
map_toronto

The geograpical coordinate of Toronto City are 43.7394839, -79.369314.


In [107]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Bathurst Quay                                                         13   
Berczy Park                                                           55   
Brockton                                                              20   
Business Reply Mail Processing Centre 969 Eastern                     17   
CN Tower                                                              13   
Cabbagetown                                                           43   
Central Bay Street                                                    84   
Chinatown                                                            100   
Christie                                                              16   
Church and Wellesley                                                  89   
Commerce Court                                                       100   
Davisville                                                            37   
Davisville North                                                      11   
Deer Park                                                             15   
Design Exchange                                                      100   
Dovercourt Village                                                    20   
Dufferin                                                              20   
Exhibition Place                                                      20   
First Canadian Place                                                 100   
Forest Hill North                                                      4   
Forest Hill SE                                                        15   
Forest Hill West                                                       4   
Garden District                                                      100   
Grange Park                                                          100   
Harbord                                                               36   
Harbourfront                                                          48   
Harbourfront East                                                    100   
Harbourfront West                                                     13   
High Park                                                             25   
...                                                                  ...   
Rathnelly                                                             15   
Regent Park                                                           48   
Richmond                                                             100   
Riverdale                                                             42   
Roncesvalles                                                          15   
Rosedale                                                               4   
Roselawn                                                               1   
Runnymede                                                             39   
Ryerson                                                              100   
South Hill                                                            15   
South Niagara                                                         13   
St. James Town                                                       143   
Stn A PO Boxes 25 The Esplanade                                       97   
Studio District                                                       37   
Summerhill East                                                        4   
Summerhill West                                                       15   
Swansea                                                               39   
The Annex                                                             25   
The Beaches                                                            4   
The Beaches West                                                      22   
The Danforth West      

In [108]:
# the number of categories have
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 240 uniques categories.


### PART 4: Analyse each neighborhood to find top venues

In [109]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")
#for item in toronto_venues['Venue Category']:
#    print (item)
#    if item == 'Neighborhood':
#        print ("YES Nei")
#if 'Neighborhood' in list(toronto_onehot.columns): 
#    print ("YES")
# add neighborhood column back to dataframe
toronto_onehot['Neighbor'] = toronto_venues['Neighborhood'] 
#print (toronto_venues['Neighborhood'])
# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbor  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Harbourfront                  0               0                  0   
1  Harbourfront                  0               0                  0   
2  Harbourfront                  0               0                  0   
3  Harbourfront                  0               0                  0   
4  Harbourfront                  0               0                  0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal     ...       Thrift / Vintage Store  Toy / Game Store  \
0                 0     ...                            0                 0   
1                 0     ...                            0                 0   
2                 0     ...                            0                 0   
3                 0     ...                            0                 0   
4                 0     ...                            0                 0   

   Trail  Train Station  Vegetarian / Vegan Restaurant  Video Game Store  \
0      0              0                              0                 0   
1      0              0                              0                 0   
2      0              0                              0                 0   
3      0              0                              0                 0   
4      0              0                              0                 0   

   Vietnamese Restaurant  Wine Bar  Wings Joint  Yoga Studio  
0                      0         0            0            0  
1                      0         0            0            0  
2                      0         0            0            0  
3                      0         0            0            0  
4                      0         0            0            0  

[5 rows x 241 columns]

In [110]:
toronto_onehot.shape
#toronto_onehot.dtypes

(3299, 241)

In [111]:
toronto_grouped = toronto_onehot.groupby(['Neighbor']).mean().reset_index()
toronto_grouped

Neighbor  Accessories Store  \
0                                            Adelaide           0.010000   
1                                       Bathurst Quay           0.000000   
2                                         Berczy Park           0.000000   
3                                            Brockton           0.000000   
4   Business Reply Mail Processing Centre 969 Eastern           0.000000   
5                                            CN Tower           0.000000   
6                                         Cabbagetown           0.000000   
7                                  Central Bay Street           0.000000   
8                                           Chinatown           0.000000   
9                                            Christie           0.000000   
10                               Church and Wellesley           0.000000   
11                                     Commerce Court           0.000000   
12                                         Davisville           0.000000   
13                                   Davisville North           0.000000   
14                                          Deer Park           0.000000   
15                                    Design Exchange           0.000000   
16                                 Dovercourt Village           0.000000   
17                                           Dufferin           0.000000   
18                                   Exhibition Place           0.000000   
19                               First Canadian Place           0.000000   
20                                  Forest Hill North           0.000000   
21                                     Forest Hill SE           0.000000   
22                                   Forest Hill West           0.000000   
23                                    Garden District           0.000000   
24                                        Grange Park           0.000000   
25                                            Harbord           0.000000   
26                                       Harbourfront           0.000000   
27                                  Harbourfront East           0.000000   
28                                  Harbourfront West           0.000000   
29                                          High Park           0.000000   
..                                                ...                ...   
43                                          Rathnelly           0.000000   
44                                        Regent Park           0.000000   
45                                           Richmond           0.010000   
46                                          Riverdale           0.000000   
47                                       Roncesvalles           0.000000   
48                                           Rosedale           0.000000   
49                                           Roselawn           0.000000   
50                                          Runnymede           0.000000   
51                                            Ryerson           0.000000   
52                                         South Hill           0.000000   
53                                      South Niagara           0.000000   
54                                     St. James Town           0.006993   
55                    Stn A PO Boxes 25 The Esplanade           0.000000   
56                                    Studio District           0.000000   
57                                    Summerhill East           0.000000   
58                                    Summerhill West           0.000000   
59                                            Swansea           0.000000   
60                                          The Annex           0.000000   
61                                        The Beaches           0.000000   
62                                   The Beaches West           0.000000   
63                                  The Danforth West           0.000000   
64               

In [112]:
num_top_venues = 5

for hood in toronto_grouped['Neighbor']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbor'] == hood].T.reset_index()
    #print (manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T)
    temp.columns = ['venue','freq']

    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
             venue  freq
0      Coffee Shop  0.06
1             Café  0.04
2  Thai Restaurant  0.04
3       Steakhouse  0.04
4              Bar  0.04


----Bathurst Quay----
              venue  freq
0    Airport Lounge  0.15
1   Airport Service  0.15
2  Airport Terminal  0.15
3             Plane  0.08
4           Airport  0.08


----Berczy Park----
            venue  freq
0     Coffee Shop  0.07
1    Cocktail Bar  0.05
2      Restaurant  0.04
3      Steakhouse  0.04
4  Farmers Market  0.04


----Brockton----
            venue  freq
0  Breakfast Spot  0.10
1            Café  0.10
2     Coffee Shop  0.10
3             Gym  0.05
4   Burrito Place  0.05


----Business Reply Mail Processing Centre 969 Eastern----
                venue  freq
0  Light Rail Station  0.12
1                 Spa  0.06
2       Auto Workshop  0.06
3                Park  0.06
4          Comic Shop  0.06


----CN Tower----
              venue  freq
0    Airport Lounge  0.15
1   Airport Service  0.15

In [113]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [114]:
# this code get top 10 of venue category of neighborhood

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighbor']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue  \
0                                            Adelaide           Coffee Shop   
1                                       Bathurst Quay        Airport Lounge   
2                                         Berczy Park           Coffee Shop   
3                                            Brockton        Breakfast Spot   
4   Business Reply Mail Processing Centre 969 Eastern    Light Rail Station   
5                                            CN Tower        Airport Lounge   
6                                         Cabbagetown           Coffee Shop   
7                                  Central Bay Street           Coffee Shop   
8                                           Chinatown                  Café   
9                                            Christie                  Café   
10                               Church and Wellesley   Japanese Restaurant   
11                                     Commerce Court           Coffee Shop   
12                                         Davisville           Pizza Place   
13                                   Davisville North           Pizza Place   
14                                          Deer Park           Coffee Shop   
15                                    Design Exchange           Coffee Shop   
16                                 Dovercourt Village              Pharmacy   
17                                           Dufferin              Pharmacy   
18                                   Exhibition Place        Breakfast Spot   
19                               First Canadian Place           Coffee Shop   
20                                  Forest Hill North                  Park   
21                                     Forest Hill SE           Coffee Shop   
22                                   Forest Hill West                  Park   
23                                    Garden District           Coffee Shop   
24                                        Grange Park                  Café   
25                                            Harbord                  Café   
26                                       Harbourfront           Coffee Shop   
27                                  Harbourfront East           Coffee Shop   
28                                  Harbourfront West        Airport Lounge   
29                                          High Park                   Bar   
..                                                ...                   ...   
43                                          Rathnelly           Coffee Shop   
44                                        Regent Park           Coffee Shop   
45                                           Richmond           Coffee Shop   
46                                          Riverdale      Greek Restaurant   
47                                       Roncesvalles        Breakfast Spot   
48                                           Rosedale                  Park   
49                                           Roselawn                Garden   
50                                          Runnymede           Coffee Shop   
51                                            Ryerson           Coffee Shop   
52                                         South Hill           Coffee Shop   
53                                      South Niagara        Airport Lounge   
54                                     St. James Town           Coffee Shop   
55                    Stn A PO Boxes 25 The Esplanade           Coffee Shop   
56                                    Studio District                  Café   
57                                    Summerhill East            Restaurant   
58                                    Summerhill West           Coffee Shop   
59                                            Swansea           Coffee Shop   
60                                          The Annex           Coffee Shop   
61                                        The Beaches     Health Food Store   
62          

### PART 5: Cluster Neighborhoods

In [115]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 4

toronto_grouped_clustering = toronto_grouped.drop('Neighbor', 1)
#print (toronto_grouped_clustering)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 2, 3, 3, 3, 2, 3, 3, 3, 3], dtype=int32)

In [116]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
#print (neighborhoods_venues_sorted)

toronto_merged = df_toronto_in_name
df_toronto_in_name.rename(columns={'Neighbourhood':'Neighborhood'},inplace=True)
print (df_toronto_in_name.columns)
print (neighborhoods_venues_sorted.columns)

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Index(['Postcode', 'Borough', 'Neighborhood', 'Latitude', 'Longitude'], dtype='object')
Index(['Cluster Labels', 'Neighborhood', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue'],
      dtype='object')


/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/pandas/core/frame.py:3027: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)


Postcode           Borough     Neighborhood   Latitude  Longitude  \
2       M5A  Downtown Toronto     Harbourfront  43.654260 -79.360636   
3       M5A  Downtown Toronto      Regent Park  43.654260 -79.360636   
13      M5B  Downtown Toronto          Ryerson  43.657162 -79.378937   
14      M5B  Downtown Toronto  Garden District  43.657162 -79.378937   
27      M5C  Downtown Toronto   St. James Town  43.651494 -79.375418   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
2                3           Coffee Shop                  Café   
3                3           Coffee Shop                  Café   
13               3           Coffee Shop        Clothing Store   
14               3           Coffee Shop        Clothing Store   
27               3           Coffee Shop            Restaurant   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
2                 Bakery                   Pub                       Park   
3                 Bakery                   Pub                       Park   
13                  Café        Cosmetics Shop  Middle Eastern Restaurant   
14                  Café        Cosmetics Shop  Middle Eastern Restaurant   
27                  Café                 Hotel                     Bakery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2         Breakfast Spot    Mexican Restaurant               Theater   
3         Breakfast Spot    Mexican Restaurant               Theater   
13    Italian Restaurant               Theater           Pizza Place   
14    Italian Restaurant               Theater           Pizza Place   
27        Breakfast Spot    Italian Restaurant             Gastropub   

   9th Most Common Venue 10th Most Common Venue  
2     Italian Restaurant          Historic Site  
3     Italian Restaurant          Historic Site  
13   Japanese Restaurant                  Diner  
14   Japanese Restaurant                  Diner  
27                 Diner            Pizza Place

Visualizing the clusters.

In [117]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters